## Video demo
#### Don't run below cell so you can see the video!

In [1]:
# don't run this cell so you can see a demo video of project

import base64
from IPython.display import HTML

def video_to_base64(video_path):
    with open(video_path, "rb") as video_file:
        video_base64 = base64.b64encode(video_file.read()).decode('utf-8')
    return video_base64

video_path = "video.mp4"
video_base64 = video_to_base64(video_path)

video_html = f'''
<video width="480" height="400" controls>
  <source src="data:video/mp4;base64,{video_base64}" type="video/mp4">
  Your browser does not support the video tag.
</video>
'''

HTML(video_html)

## Codes

In [2]:
import cv2
import numpy as np
import matplotlib.pyplot as plt
from IPython.display import clear_output

In [3]:
# function to draw Player 1 sign on nearest section of board
def draw_cross(center_coordinates):
    cv2.ellipse(img, center=(center_coordinates[0], center_coordinates[1]), axes=(100, 1), angle=45, startAngle=0, endAngle=360, color=(255, 0, 0), thickness=10)
    cv2.ellipse(img, center=(center_coordinates[0], center_coordinates[1]), axes=(100, 1), angle=-45, startAngle=0, endAngle=360, color=(255, 0, 0), thickness=10)

In [4]:
# function to draw Player 2 sign on nearest section of board
def draw_circle(center_coordinates):
    cv2.circle(img, center=(center_coordinates[0], center_coordinates[1]), radius=80, color=(0, 0, 255), thickness=3)    

In [5]:
# function to calculate euclidean_distance between two points
def euclidean_distance(point1, point2):
    return np.sqrt((point1[0] - point2[0]) ** 2 + (point1[1] - point2[1]) ** 2)

In [6]:
# function to return nearest center coordinates and it's section to clicked coordinates using euclidean_distance
def closest_center(clicked_coordinates):
    distances = [euclidean_distance(clicked_coordinates, center) for center in centers_list]
    return centers_list[distances.index(min(distances))], distances.index(min(distances))

In [7]:
# function to return the winner if there is one
# winner is the person filled a row, a column or a diameter sooner
def check_winner(arr):
    # Check rows and columns
    for i in range(3):
        if np.all(arr[i, :] == arr[i, 0]) and arr[i, 0] != 0:
            return arr[i, 0]
        if np.all(arr[:, i] == arr[0, i]) and arr[0, i] != 0:
            return arr[0, i]

    # Check diagonals
    if np.all(np.diag(arr) == arr[0, 0]) and arr[0, 0] != 0:
        return arr[0, 0]
    if np.all(np.diag(np.fliplr(arr)) == arr[0, 2]) and arr[0, 2] != 0:
        return arr[0, 2]

    return None  

In [8]:
# function listening to mouse events
def callback_function(event, x, y, flag, param):
    global player_turn, game_end, img, board_status
    cv2.imshow("Tic-Tac-Toe", img)
    if event == cv2.EVENT_LBUTTONDOWN:
        if game_end:
            clear_output(wait=True)
            print("Game Ended. Restart with r or Quit with pressing q")
            key = cv2.waitKey()
            if key == ord("q"):
                cv2.destroyAllWindows()
            elif key == ord("r"):
                player_turn = 1
                game_end = False
                board_status = np.zeros((3, 3))
                img = board_img.copy()
                
        elif player_turn == 1:
            clear_output(wait=True)
            print("Player 1 clicked")
            clicked_coordinates = (x, y)
            cliked_center, cliked_center_index = closest_center(clicked_coordinates)
            if board_status.flat[cliked_center_index] == 0:
                draw_cross(cliked_center)
                board_status.flat[cliked_center_index] = 1
                winner = check_winner(board_status)
                if winner:
                    print(f"Player {winner} is the winner!")
                    game_end = True
                elif (not winner) and (0 not in board_status):
                    print("It's a tie!")
                    game_end = True
                player_turn = 2
            else:
                print("Already taken!")
        else:
            print("Not Your Turn Player 1!")
            clear_output(wait=True)
            
    elif event == cv2.EVENT_RBUTTONDOWN:
        if game_end:
            clear_output(wait=True)
            print("Game Ended. Restart with r or Quit with pressing q")
            key = cv2.waitKey()
            if key == ord("q"):
                cv2.destroyAllWindows()
            elif key == ord("r"):
                player_turn = 1
                game_end = False
                board_status = np.zeros((3, 3))
                img = board_img.copy()
                
        elif player_turn == 2:
            clear_output(wait=True)
            print("Player 2 clicked")
            clicked_coordinates = (x, y)
            cliked_center, cliked_center_index = closest_center(clicked_coordinates)
            if board_status.flat[cliked_center_index] == 0:
                draw_circle(cliked_center)
                board_status.flat[cliked_center_index] = 2
                winner = check_winner(board_status)
                if winner:
                    print(f"Player {winner} is the winner!")
                    game_end = True
                elif (not winner) and (0 not in board_status):
                    print("It's a tie!")
                    game_end = True  
                player_turn = 1
            else:
                print("Already taken!")
        else:
            print("Not Your Turn Player 2!")
            clear_output(wait=True)

In [9]:
img = 255 * np.ones((600, 600, 3), dtype=np.uint8)

# game background
cv2.line(img, pt1=(200, 0), pt2=(200, 600), color=(0, 0, 0), thickness=4)
cv2.line(img, pt1=(400, 0), pt2=(400, 600), color=(0, 0, 0), thickness=4)
cv2.line(img, pt1=(0, 200), pt2=(600, 200), color=(0, 0, 0), thickness=4)
cv2.line(img, pt1=(0, 400), pt2=(600, 400), color=(0, 0, 0), thickness=4)

# board 9 sections center coordinates
centers_list = [(100, 100), (300, 100), (500, 100),
                (100, 300), (300, 300), (500, 300),
                (100, 500), (300, 500), (500, 500)]

player_turn = 1
game_end = False
board_status = np.zeros((3, 3))
board_img = img.copy()
cv2.namedWindow("Tic-Tac-Toe", cv2.WINDOW_AUTOSIZE)
cv2.setWindowProperty("Tic-Tac-Toe", cv2.WND_PROP_TOPMOST, 1)
cv2.imshow("Tic-Tac-Toe", img)
cv2.setMouseCallback("Tic-Tac-Toe", callback_function)


cv2.waitKey()
cv2.destroyAllWindows()

Player 1 clicked
Player 1.0 is the winner!
